# Imports

In [1]:
import sys                                                                      
import argparse
import numpy as np
import pandas as pd

sys.path.append("../../code/src/")
import lds_functions

# Get mouse positions

In [2]:
# tracking data filename
data_filename = "../../data/postions_session003_start0.00_end15548.27.csv"
start_position = 0       # filtering start position
number_positions = 10000 # filtering number of positions
data = pd.read_csv(filepath_or_buffer=data_filename)
data = data.iloc[start_position:start_position+number_positions,:]
y = np.transpose(data[["x", "y"]].to_numpy())
date_times = pd.to_datetime(data["time"])

# Define the linear dynamical system parameters

In [3]:
sigma_a = 0.1            # standard deviation of acceleration
sigma_x = 0.001          # standard deviation of x coordinate of position
sigma_y = 0.001          # standard deviation of y coordinate of position
V0_diag_value0 = 0.001   # initial state variance

# Taken from the book
# barShalomEtAl01-estimationWithApplicationToTrackingAndNavigation.pdf
# section 6.3.3
dt = (date_times[1]-date_times[0]).total_seconds()
# Eq. 6.3.3-2
B = np.array([[1, dt, .5*dt**2, 0, 0, 0],
              [0, 1, dt, 0, 0, 0],
              [0, 0, 1, 0, 0, 0],
              [0, 0, 0, 1, dt, .5*dt**2],
              [0, 0, 0, 0, 1, dt],
              [0, 0, 0, 0, 0, 1]],
             dtype=np.double)
Z = np.array([[1, 0, 0, 0, 0, 0],
              [0, 0, 0, 1, 0, 0]],
             dtype=np.double)
# Eq. 6.3.3-4
Q = np.array([[dt**4/4, dt**3/2, dt**2/2, 0, 0, 0],
              [dt**3/2, dt**2,   dt,      0, 0, 0],
              [dt**2/2, dt,      1,       0, 0, 0],
              [0, 0, 0, dt**4/4, dt**3/2, dt**2/2],
              [0, 0, 0, dt**3/2, dt**2,   dt],
              [0, 0, 0, dt**2/2, dt,      1]],
             dtype=np.double)*sigma_a**2
R = np.diag([sigma_x**2, sigma_y**2])
m0 = np.array([y[0, 0], 0, 0, y[1, 0], 0, 0], dtype=np.double)
V0 = np.diag(np.ones(len(m0))*V0_diag_value0)

# Run Kalman filter and smoother

In [4]:
filterRes = lds_functions.filterLDS_SS_withMissingValues(y=y, B=B, Q=Q,
                                                         m0=m0, V0=V0, Z=Z,
                                                         R=R)
smoothRes = lds_functions.smoothLDS_SS(B=B,
                                       xnn=filterRes["xnn"],
                                       Vnn=filterRes["Vnn"],
                                       xnn1=filterRes["xnn1"],
                                       Vnn1=filterRes["Vnn1"],
                                       m0=m0, V0=V0)

# Plot measures, filtered and smoothed mouse positions

In [5]:
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objects as go

fig = go.Figure()
trace_pos = go.Scatter(x=y[0,:], y=y[1,:],
                       mode="markers",
                       marker={"color": "black"},
                       customdata=data["time"],
                       hovertemplate="<b>x:</b>%{x:.3f}<br><b>y</b>:%{y:.3f}<br><b>time</b>:%{customdata} sec",
                       name="measured",
                       showlegend=True
                      )
trace_filtered = go.Scatter(x=filterRes["xnn"][0,0,:],
                            y=filterRes["xnn"][3,0,:],
                            mode="markers",
                            marker={"color": "red"},
                            customdata=data["time"],
                            hovertemplate="<b>x:</b>%{x:.3f}<br><b>y</b>:%{y:.3f}<br><b>time</b>:%{customdata} sec",
                            name="filtered",
                            showlegend=True,
                           )
trace_smoothed = go.Scatter(x=smoothRes["xnN"][0,0,:],
                            y=smoothRes["xnN"][3,0,:],
                            mode="markers",
                            marker={"color": "green"},
                            customdata=data["time"],
                            hovertemplate="<b>x:</b>%{x:.3f}<br><b>y</b>:%{y:.3f}<br><b>time</b>:%{customdata} sec",
                            name="smoothed",
                            showlegend=True,
                           )
iplot([trace_pos, trace_filtered, trace_smoothed])